<a href="https://colab.research.google.com/github/Niranjan1422/Infosys_Internship/blob/main/Infosys_Chat%26Support_Data_Ingestion.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [1]:
import json
import pandas as pd
import numpy as np
import re
from datetime import datetime
from sklearn.preprocessing import MinMaxScaler, LabelEncoder

In [19]:
import json
import pandas as pd
import re

def load_robustly(file_path):
    records = []
    malformed_objects_count = 0
    try:
        with open(file_path, "r", encoding="utf-8", errors="ignore") as f:
            content = f.read()

        # Strip outer brackets if it's a single JSON array
        cleaned_content = content.strip()
        if cleaned_content.startswith('[') and cleaned_content.endswith(']') and len(cleaned_content) > 2:
            cleaned_content = cleaned_content[1:-1]

        # Replace '},{' with '}\n{' to get each object on a new line for easier parsing
        object_strings = re.split(r'}\s*,\s*\{', cleaned_content)

        # Reconstruct full object strings with their braces
        parsed_object_strings = []
        if len(object_strings) == 1 and object_strings[0].strip(): # Single object case
            parsed_object_strings.append(object_strings[0].strip())
        elif len(object_strings) > 1: # Multiple objects
            parsed_object_strings.append(object_strings[0].strip() + '}')
            for i in range(1, len(object_strings) - 1):
                parsed_object_strings.append('{' + object_strings[i].strip() + '}')
            parsed_object_strings.append('{' + object_strings[-1].strip())

        for i, obj_str in enumerate(parsed_object_strings):
            obj_str = obj_str.strip()
            if not obj_str:
                continue
            # Ensure the string is wrapped in braces before attempting to parse
            if not obj_str.startswith('{'):
                obj_str = '{' + obj_str
            if not obj_str.endswith('}'):
                obj_str = obj_str + '}'

            try:
                records.append(json.loads(obj_str))
            except json.JSONDecodeError as e:
                malformed_objects_count += 1
                # print(f"Skipped malformed object (index {i}) in {file_path}. Error: {e}. Content start: {obj_str[:100]}...")
            except Exception as e:
                malformed_objects_count += 1
                # print(f"Skipped object (index {i}) due to unexpected error in {file_path}. Error: {e}. Content start: {obj_str[:100]}...")

    except Exception as e:
        print(f"An unexpected error occurred while reading or processing {file_path}: {e}")
        return [] # Return empty list on major file processing errors

    print(f"Successfully loaded {len(records)} records from {file_path}.")
    print(f"Skipped {malformed_objects_count} malformed objects from {file_path}.")
    return records

cleaned_data = load_robustly(
    "/content/drive/MyDrive/Infosys_Datasets/cleaned_enron_emails.json"
)
threaded_data = load_robustly(
    "/content/drive/MyDrive/Infosys_Datasets/threaded_emails.json"
)

cleaned_df = pd.DataFrame(cleaned_data)
threaded_df = pd.DataFrame(threaded_data)

print(f"cleaned_df shape: {cleaned_df.shape}")
print(f"threaded_df shape: {threaded_df.shape}")

Successfully loaded 136108 records from /content/drive/MyDrive/Infosys_Datasets/cleaned_enron_emails.json.
Skipped 2 malformed objects from /content/drive/MyDrive/Infosys_Datasets/cleaned_enron_emails.json.
Successfully loaded 10004 records from /content/drive/MyDrive/Infosys_Datasets/threaded_emails.json.
Skipped 12728 malformed objects from /content/drive/MyDrive/Infosys_Datasets/threaded_emails.json.
cleaned_df shape: (136108, 7)
threaded_df shape: (10004, 11)


In [4]:
cleaned_df.head()
threaded_df.head()

Empty DataFrame
Columns: []
Index: []

In [5]:
!sed -n '971300,971330p' /content/drive/MyDrive/Infosys_Datasets/cleaned_enron_emails.json

  {
    "From": "twanda.sweet@enron.com",
    "To": "aleck.dadson@enron.com",
    "Subject": "Project Stanley",
    "Date": "Mon, 12 Jun 2000 10:50:00 -0700",
    "Body": "Mr. Dadson, please be advised that a conference call regarding the\nabove-referenced matter has been scheduled for this Thursday at 9:00am\ncentral standard time.  The participants are as follows:\n\nRichard Sanders\nRob Hemstock (Calgary)\nRick Shapiro\nAl Dadson\n\nPlease let me know if this time is not convenient for you.  Also, please\nprovide me with a phone number.  The number that we currently have in the\nEnron directory is not a working number (416-214-1740).\n\nThanks\nTwanda\n713-853-9402",
    "ThreadKey": "project stanley::Mon, 12 Jun 2000 10:50:00 -0700",
    "Filename": "175."
  },
  {
    "From": "richard.sanders@enron.com",
    "To": "robert.williams@enron.com",
    "Subject": "Re: FW: Strategy & End Game for FERC Proceeding",
    "Date": "Mon, 08 Jan 2001 02:32:00 -0800",
    "Body": "This is an ENA

In [6]:
import json
import pandas as pd

def load_json_safely(file_path):
    records = []
    bad_lines = 0

    with open(file_path, "r", encoding="utf-8", errors="ignore") as f:
        for i, line in enumerate(f, start=1):
            try:
                records.append(json.loads(line))
            except json.JSONDecodeError:
                bad_lines += 1

    print(f"Loaded records: {len(records)}")
    print(f"Skipped corrupted lines: {bad_lines}")
    return records

cleaned_data = load_json_safely(
    "/content/drive/MyDrive/Infosys_Datasets/cleaned_enron_emails.json"
)

threaded_data = load_json_safely(
    "/content/drive/MyDrive/Infosys_Datasets/threaded_emails.json"
)

cleaned_df = pd.DataFrame(cleaned_data)
threaded_df = pd.DataFrame(threaded_data)

Loaded records: 0
Skipped corrupted lines: 1045489
Loaded records: 0
Skipped corrupted lines: 1278561


In [8]:
import pandas as pd
import json

try:
    cleaned_df = pd.read_json(
        "/content/drive/MyDrive/Infosys_Datasets/cleaned_enron_emails.json",
        encoding="utf-8",
        encoding_errors="ignore"
    )
except (ValueError, json.JSONDecodeError) as e:
    print(f"Error loading cleaned_enron_emails.json: {e}")
    cleaned_df = pd.DataFrame() # Initialize as empty DataFrame on error

try:
    threaded_df = pd.read_json(
        "/content/drive/MyDrive/Infosys_Datasets/threaded_emails.json",
        encoding="utf-8",
        encoding_errors="ignore"
    )
except (ValueError, json.JSONDecodeError) as e:
    print(f"Error loading threaded_emails.json: {e}")
    threaded_df = pd.DataFrame() # Initialize as empty DataFrame on error

print(cleaned_df.shape)
print(threaded_df.shape)

Error loading cleaned_enron_emails.json: Unmatched ''"' when when decoding 'string'
Error loading threaded_emails.json: Unmatched ''"' when when decoding 'string'
(0, 0)
(0, 0)


In [9]:
!head -n 5 /content/drive/MyDrive/Infosys_Datasets/cleaned_enron_emails.json

[
  {
    "From": "",
    "To": "",
    "Subject": "",


In [10]:
import re
import json
import pandas as pd

file_path = "/content/drive/MyDrive/Infosys_Datasets/cleaned_enron_emails.json"

with open(file_path, "r", encoding="utf-8", errors="ignore") as f:
    raw_text = f.read()

print("Raw file loaded")
print("Total characters:", len(raw_text))

Raw file loaded
Total characters: 239075328


In [11]:
pattern = re.compile(r"\{.*?\}", re.DOTALL)

matches = pattern.findall(raw_text)

print("Potential records found:", len(matches))

Potential records found: 121942


In [12]:
records = []
failed = 0

for obj in matches:
    try:
        # Fix common quote issues
        fixed = obj.replace('\n', ' ').replace('\r', ' ')
        records.append(json.loads(fixed))
    except json.JSONDecodeError:
        failed += 1

print("Recovered records:", len(records))
print("Failed records:", failed)

Recovered records: 120946
Failed records: 996


In [13]:
cleaned_df = pd.DataFrame(records)

print("Final DataFrame Shape:", cleaned_df.shape)
cleaned_df.head()

Final DataFrame Shape: (120946, 7)


From                                                 To  \
0                                                                               
1                                                                               
2          msagel@home.com                                  jarnold@enron.com   
3  slafontaine@globalp.com                              john.arnold@enron.com   
4  iceoperations@intcx.com  icehelpdesk@intcx.com, internalmarketing@intcx...   

                         Subject                             Date  \
0                                                                   
1                                                                   
2                         Status  Thu, 16 Nov 2000 09:30:00 -0800   
3             re:summer inverses  Fri, 08 Dec 2000 05:05:00 -0800   
4  The WTI Bullet swap contracts  Tue, 15 May 2001 09:43:00 -0700   

                                                Body  \
0                                                      
1                                                      
2  John:\n?\nI'm not really sure what happened be...   
3  i suck-hope youve made more money in natgas la...   
4  Hi,\n\n\nFollowing the e-mail you have receive...   

                                           ThreadKey   Filename  
0                                                 ::  .DS_Store  
1                                                 ::  .DS_Store  
2            status::Thu, 16 Nov 2000 09:30:00 -0800        36.  
3   summer inverses::Fri, 08 Dec 2000 05:05:00 -0800        19.  
4  the wti bullet swap contracts::Tue, 15 May 200...        50.

from matplotlib import pyplot as plt
import seaborn as sns
_df_11.groupby('From').size().plot(kind='barh', color=sns.palettes.mpl_palette('Dark2'))
plt.gca().spines[['top', 'right',]].set_visible(False)

from matplotlib import pyplot as plt
import seaborn as sns
_df_12.groupby('To').size().plot(kind='barh', color=sns.palettes.mpl_palette('Dark2'))
plt.gca().spines[['top', 'right',]].set_visible(False)

from matplotlib import pyplot as plt
import seaborn as sns
_df_13.groupby('Subject').size().plot(kind='barh', color=sns.palettes.mpl_palette('Dark2'))
plt.gca().spines[['top', 'right',]].set_visible(False)

...

from matplotlib import pyplot as plt
import seaborn as sns
def _plot_series(series, series_name, series_index=0):
  palette = list(sns.palettes.mpl_palette('Dark2'))
  counted = (series['Date']
                .value_counts()
              .reset_index(name='counts')
              .rename({'index': 'Date'}, axis=1)
              .sort_values('Date', ascending=True))
  xs = counted['Date']
  ys = counted['counts']
  plt.plot(xs, ys, label=series_name, color=palette[series_index % len(palette)])

fig, ax = plt.subplots(figsize=(10, 5.2), layout='constrained')
df_sorted = _df_18.sort_values('Date', ascending=True)
for i, (series_name, series) in enumerate(df_sorted.groupby('Date')):
  _plot_series(series, series_name, i)
  fig.legend(title='Date', bbox_to_anchor=(1, 1), loc='upper left')
sns.despine(fig=fig, ax=ax)
plt.xlabel('Date')
_ = plt.ylabel('count()')

from matplotlib import pyplot as plt
import seaborn as sns
import pandas as pd
plt.subplots(figsize=(8, 8))
df_2dhist = pd.DataFrame({
    x_label: grp['To'].value_counts()
    for x_label, grp in _df_19.groupby('From')
})
sns.heatmap(df_2dhist, cmap='viridis')
plt.xlabel('From')
_ = plt.ylabel('To')

from matplotlib import pyplot as plt
import seaborn as sns
import pandas as pd
plt.subplots(figsize=(8, 8))
df_2dhist = pd.DataFrame({
    x_label: grp['Subject'].value_counts()
    for x_label, grp in _df_20.groupby('To')
})
sns.heatmap(df_2dhist, cmap='viridis')
plt.xlabel('To')
_ = plt.ylabel('Subject')

from matplotlib import pyplot as plt
import seaborn as sns
import pandas as pd
plt.subplots(figsize=(8, 8))
df_2dhist = pd.DataFrame({
    x_label: grp['Date'].value_counts()
    for x_label, grp in _df_21.groupby('Subject')
})
sns.heatmap(df_2dhist, cmap='viridis')
plt.xlabel('Subject')
_ = plt.ylabel('Date')

from matplotlib import pyplot as plt
import seaborn as sns
import pandas as pd
plt.subplots(figsize=(8, 8))
df_2dhist = pd.DataFrame({
    x_label: grp['Body'].value_counts()
    for x_label, grp in _df_22.groupby('Date')
})
sns.heatmap(df_2dhist, cmap='viridis')
plt.xlabel('Date')
_ = plt.ylabel('Body')

In [14]:
file_path = "/content/drive/MyDrive/Infosys_Datasets/threaded_emails.json"

with open(file_path, "r", encoding="utf-8", errors="ignore") as f:
    raw_text = f.read()

matches = re.findall(r"\{.*?\}", raw_text, re.DOTALL)

records = []
failed = 0

for obj in matches:
    try:
        fixed = obj.replace('\n', ' ').replace('\r', ' ')
        records.append(json.loads(fixed))
    except json.JSONDecodeError:
        failed += 1

threaded_df = pd.DataFrame(records)

print("Threaded DF Shape:", threaded_df.shape)
print("Failed records:", failed)
threaded_df.head()

Threaded DF Shape: (99372, 11)
Failed records: 1770


MessageID                     From  \
0  <17938862.1075857585990.JavaMail.evans@thyme>    john.arnold@enron.com   
1  <23987417.1075857585124.JavaMail.evans@thyme>  slafontaine@globalp.com   
2  <19171686.1075857585034.JavaMail.evans@thyme>  slafontaine@globalp.com   
3   <3552781.1075857584209.JavaMail.evans@thyme>    john.arnold@enron.com   
4  <16522398.1075857584074.JavaMail.evans@thyme>    john.arnold@enron.com   

                        To InReplyTo             Subject  \
0  slafontaine@globalp.com            re:summer inverses   
1    john.arnold@enron.com            re:summer inverses   
2    john.arnold@enron.com            re:summer inverses   
3  slafontaine@globalp.com            re:summer inverses   
4  slafontaine@globalp.com            re:summer inverses   

                              Date  \
0  Wed, 06 Dec 2000 21:38:00 -0800   
1  Thu, 07 Dec 2000 01:27:00 -0800   
2  Fri, 08 Dec 2000 05:05:00 -0800   
3  Mon, 11 Dec 2000 08:51:00 -0800   
4  Mon, 11 Dec 2000 09:04:00 -0800   

                                                Body  \
0  seems crazy.  if you're willing to ride it for...   
1  they are crazy but mite have to scale in which...   
2  i suck-hope youve made more money in natgas la...   
3  amazing how with cash futures at $1 and the ba...   
4  a couple more thoughts.  certainly losing lots...   

                                          ThreadKey Filename  \
0  summer inverses::Wed, 06 Dec 2000 21:38:00 -0800      18.   
1  summer inverses::Thu, 07 Dec 2000 01:27:00 -0800      23.   
2  summer inverses::Fri, 08 Dec 2000 05:05:00 -0800      19.   
3  summer inverses::Mon, 11 Dec 2000 08:51:00 -0800     187.   
4  summer inverses::Mon, 11 Dec 2000 09:04:00 -0800     181.   

                                      ThreadID  ThreadPosition  
0  thread-218b74fb-b061-43b7-a3a0-3935a88ec145             0.0  
1  thread-218b74fb-b061-43b7-a3a0-3935a88ec145             3.0  
2  thread-218b74fb-b061-43b7-a3a0-3935a88ec145             6.0  
3  thread-218b74fb-b061-43b7-a3a0-3935a88ec145             9.0  
4  thread-218b74fb-b061-43b7-a3a0-3935a88ec145            13.0

In [15]:
cleaned_df.head()
threaded_df.head()

MessageID                     From  \
0  <17938862.1075857585990.JavaMail.evans@thyme>    john.arnold@enron.com   
1  <23987417.1075857585124.JavaMail.evans@thyme>  slafontaine@globalp.com   
2  <19171686.1075857585034.JavaMail.evans@thyme>  slafontaine@globalp.com   
3   <3552781.1075857584209.JavaMail.evans@thyme>    john.arnold@enron.com   
4  <16522398.1075857584074.JavaMail.evans@thyme>    john.arnold@enron.com   

                        To InReplyTo             Subject  \
0  slafontaine@globalp.com            re:summer inverses   
1    john.arnold@enron.com            re:summer inverses   
2    john.arnold@enron.com            re:summer inverses   
3  slafontaine@globalp.com            re:summer inverses   
4  slafontaine@globalp.com            re:summer inverses   

                              Date  \
0  Wed, 06 Dec 2000 21:38:00 -0800   
1  Thu, 07 Dec 2000 01:27:00 -0800   
2  Fri, 08 Dec 2000 05:05:00 -0800   
3  Mon, 11 Dec 2000 08:51:00 -0800   
4  Mon, 11 Dec 2000 09:04:00 -0800   

                                                Body  \
0  seems crazy.  if you're willing to ride it for...   
1  they are crazy but mite have to scale in which...   
2  i suck-hope youve made more money in natgas la...   
3  amazing how with cash futures at $1 and the ba...   
4  a couple more thoughts.  certainly losing lots...   

                                          ThreadKey Filename  \
0  summer inverses::Wed, 06 Dec 2000 21:38:00 -0800      18.   
1  summer inverses::Thu, 07 Dec 2000 01:27:00 -0800      23.   
2  summer inverses::Fri, 08 Dec 2000 05:05:00 -0800      19.   
3  summer inverses::Mon, 11 Dec 2000 08:51:00 -0800     187.   
4  summer inverses::Mon, 11 Dec 2000 09:04:00 -0800     181.   

                                      ThreadID  ThreadPosition  
0  thread-218b74fb-b061-43b7-a3a0-3935a88ec145             0.0  
1  thread-218b74fb-b061-43b7-a3a0-3935a88ec145             3.0  
2  thread-218b74fb-b061-43b7-a3a0-3935a88ec145             6.0  
3  thread-218b74fb-b061-43b7-a3a0-3935a88ec145             9.0  
4  thread-218b74fb-b061-43b7-a3a0-3935a88ec145            13.0

In [16]:
#1️⃣ DATA CLEANING

In [17]:
#Handling Missing Values

cleaned_df.isnull().sum()

From         0
To           0
Subject      0
Date         0
Body         0
ThreadKey    0
Filename     0
dtype: int64

In [20]:
cleaned_df = cleaned_df.dropna(subset=['Body'])

In [21]:
cleaned_df.isnull().sum()

From         0
To           0
Subject      0
Date         0
Body         0
ThreadKey    0
Filename     0
dtype: int64

In [40]:
#Removing Duplicate Records

before = len(cleaned_df)
cleaned_df = cleaned_df.drop_duplicates(subset=['Body']).copy() # Added .copy() to prevent SettingWithCopyWarning
after = len(cleaned_df)

print("Duplicates removed:", before - after)

Duplicates removed: 0


In [25]:
#Correct Invalid / Inconsistent Values

cleaned_df['Subject'] = cleaned_df['Subject'].fillna("NO_SUBJECT")

/tmp/ipython-input-1171484551.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  cleaned_df['Subject'] = cleaned_df['Subject'].fillna("NO_SUBJECT")


In [28]:
cleaned_df[['Subject']].head()

Subject
0                                                   
1                                             Status
2                                 re:summer inverses
3                      The WTI Bullet swap contracts
4  Invitation: EBS/GSS Meeting w/Bristol Babcock ...

from matplotlib import pyplot as plt
import seaborn as sns
_df_23.groupby('Subject').size().plot(kind='barh', color=sns.palettes.mpl_palette('Dark2'))
plt.gca().spines[['top', 'right',]].set_visible(False)

In [30]:
#Fixing Formatting Errors

cleaned_df['Erom'] = cleaned_df['From'].str.lower().str.strip()
cleaned_df['To'] = cleaned_df['To'].str.lower().str.strip()

In [32]:
cleaned_df[['From', 'To']].head()

From  \
0                              
1            msagel@home.com   
2    slafontaine@globalp.com   
3    iceoperations@intcx.com   
4  jeff.youngflesh@enron.com   

                                                  To  
0                                                     
1                                  jarnold@enron.com  
2                              john.arnold@enron.com  
3  icehelpdesk@intcx.com, internalmarketing@intcx...  
4  anthony.gilmore@enron.com, colleen.koenig@enro...

from matplotlib import pyplot as plt
import seaborn as sns
_df_24.groupby('From').size().plot(kind='barh', color=sns.palettes.mpl_palette('Dark2'))
plt.gca().spines[['top', 'right',]].set_visible(False)

from matplotlib import pyplot as plt
import seaborn as sns
_df_25.groupby('To').size().plot(kind='barh', color=sns.palettes.mpl_palette('Dark2'))
plt.gca().spines[['top', 'right',]].set_visible(False)

from matplotlib import pyplot as plt
import seaborn as sns
import pandas as pd
plt.subplots(figsize=(8, 8))
df_2dhist = pd.DataFrame({
    x_label: grp['To'].value_counts()
    for x_label, grp in _df_26.groupby('From')
})
sns.heatmap(df_2dhist, cmap='viridis')
plt.xlabel('From')
_ = plt.ylabel('To')

In [33]:
#2️⃣ DATA VALIDATION

In [34]:
#Schema Validation

expected_columns = ['From', 'To', 'Subject', 'Body', 'Date']
missing_cols = set(expected_columns) - set(cleaned_df.columns)

print("Missing columns:", missing_cols)

Missing columns: set()


In [36]:
#Mandatory Field Checks

mandatory_check = cleaned_df[['From', 'To', 'Body']].isnull().sum()
mandatory_check

From    0
To      0
Body    0
dtype: int64

In [38]:
#Range / Logical Checks

invalid_dates = cleaned_df['Date'].isnull().sum()
print("Invalid Dates:", invalid_dates)

Invalid Dates: 0


In [41]:
#Referential Integrity (Threads)

threaded_df[['ThreadID']].head()

ThreadID
0  thread-218b74fb-b061-43b7-a3a0-3935a88ec145
1  thread-218b74fb-b061-43b7-a3a0-3935a88ec145
2  thread-218b74fb-b061-43b7-a3a0-3935a88ec145
3  thread-7073203c-410c-43da-a3bc-551e58f31f9f
4  thread-7073203c-410c-43da-a3bc-551e58f31f9f

from matplotlib import pyplot as plt
import seaborn as sns
_df_27.groupby('ThreadID').size().plot(kind='barh', color=sns.palettes.mpl_palette('Dark2'))
plt.gca().spines[['top', 'right',]].set_visible(False)

In [42]:
#3️⃣ DATA TRANSFORMATION

In [44]:
#Data Type Conversion

cleaned_df['Date'] = pd.to_datetime(cleaned_df['Date'], errors='coerce', utc=True)

In [45]:
cleaned_df.dtypes

From                      object
To                        object
Subject                   object
Date         datetime64[ns, UTC]
Body                      object
ThreadKey                 object
Filename                  object
Erom                      object
dtype: object

In [46]:
#Unit Conversion (Timezone → UTC)

cleaned_df['Date_utc'] = cleaned_df['Date'].dt.tz_convert('UTC')
cleaned_df[['Date_utc']].head()

Date_utc
0                       NaT
1 2000-11-16 17:30:00+00:00
2 2000-12-08 13:05:00+00:00
3 2001-05-15 16:43:00+00:00
4 2000-11-27 09:49:00+00:00

from matplotlib import pyplot as plt
import seaborn as sns
def _plot_series(series, series_name, series_index=0):
  palette = list(sns.palettes.mpl_palette('Dark2'))
  counted = (series['Date_utc']
                .value_counts()
              .reset_index(name='counts')
              .rename({'index': 'Date_utc'}, axis=1)
              .sort_values('Date_utc', ascending=True))
  xs = counted['Date_utc']
  ys = counted['counts']
  plt.plot(xs, ys, label=series_name, color=palette[series_index % len(palette)])

fig, ax = plt.subplots(figsize=(10, 5.2), layout='constrained')
df_sorted = _df_28.sort_values('Date_utc', ascending=True)
_plot_series(df_sorted, '')
sns.despine(fig=fig, ax=ax)
plt.xlabel('Date_utc')
_ = plt.ylabel('count()')

from matplotlib import pyplot as plt
import seaborn as sns
def _plot_series(series, series_name, series_index=0):
  palette = list(sns.palettes.mpl_palette('Dark2'))
  counted = (series['Date_utc']
                .value_counts()
              .reset_index(name='counts')
              .rename({'index': 'Date_utc'}, axis=1)
              .sort_values('Date_utc', ascending=True))
  xs = counted['Date_utc']
  ys = counted['counts']
  plt.plot(xs, ys, label=series_name, color=palette[series_index % len(palette)])

fig, ax = plt.subplots(figsize=(10, 5.2), layout='constrained')
df_sorted = _df_29.sort_values('Date_utc', ascending=True)
_plot_series(df_sorted, '')
sns.despine(fig=fig, ax=ax)
plt.xlabel('Date_utc')
_ = plt.ylabel('count()')

In [48]:
#Normalization

cleaned_df['email_length'] = cleaned_df['Body'].apply(len)

scaler = MinMaxScaler()
cleaned_df['email_length_norm'] = scaler.fit_transform(
    cleaned_df[['email_length']]
)

cleaned_df[['email_length', 'email_length_norm']].head()

email_length  email_length_norm
0             0           0.000000
1           600           0.000428
2           275           0.000196
3          1066           0.000760
4           198           0.000141

from matplotlib import pyplot as plt
_df_30['email_length'].plot(kind='hist', bins=20, title='email_length')
plt.gca().spines[['top', 'right',]].set_visible(False)

from matplotlib import pyplot as plt
_df_31['email_length_norm'].plot(kind='hist', bins=20, title='email_length_norm')
plt.gca().spines[['top', 'right',]].set_visible(False)

from matplotlib import pyplot as plt
_df_32.plot(kind='scatter', x='email_length', y='email_length_norm', s=32, alpha=.8)
plt.gca().spines[['top', 'right',]].set_visible(False)

from matplotlib import pyplot as plt
_df_33['email_length'].plot(kind='line', figsize=(8, 4), title='email_length')
plt.gca().spines[['top', 'right']].set_visible(False)

from matplotlib import pyplot as plt
_df_34['email_length_norm'].plot(kind='line', figsize=(8, 4), title='email_length_norm')
plt.gca().spines[['top', 'right']].set_visible(False)

In [50]:
#Aggregation (Daily → Monthly)

cleaned_df['month'] = cleaned_df['Date_utc'].dt.to_period('M')

monthly_counts = cleaned_df.groupby('month').size().reset_index(name='email_count')
monthly_counts.head()

/tmp/ipython-input-939154425.py:3: UserWarning: Converting to PeriodArray/Index representation will drop timezone information.
  cleaned_df['month'] = cleaned_df['Date_utc'].dt.to_period('M')


month  email_count
0  1980-01          109
1  1998-01            1
2  1998-05            1
3  1999-02            4
4  1999-03            5

from matplotlib import pyplot as plt
_df_35['email_count'].plot(kind='hist', bins=20, title='email_count')
plt.gca().spines[['top', 'right',]].set_visible(False)

from matplotlib import pyplot as plt
_df_36['email_count'].plot(kind='line', figsize=(8, 4), title='email_count')
plt.gca().spines[['top', 'right']].set_visible(False)

In [52]:
#Encoding (Categorical → Numeric)

encoder = LabelEncoder()
cleaned_df['sender_id'] = encoder.fit_transform(cleaned_df['From'])

cleaned_df[['From', 'sender_id']].head()

From  sender_id
0                                     0
1            msagel@home.com       4806
2    slafontaine@globalp.com       6175
3    iceoperations@intcx.com       2720
4  jeff.youngflesh@enron.com       3050

from matplotlib import pyplot as plt
_df_37['sender_id'].plot(kind='hist', bins=20, title='sender_id')
plt.gca().spines[['top', 'right',]].set_visible(False)

from matplotlib import pyplot as plt
import seaborn as sns
_df_38.groupby('From').size().plot(kind='barh', color=sns.palettes.mpl_palette('Dark2'))
plt.gca().spines[['top', 'right',]].set_visible(False)

from matplotlib import pyplot as plt
_df_39['sender_id'].plot(kind='line', figsize=(8, 4), title='sender_id')
plt.gca().spines[['top', 'right']].set_visible(False)

<string>:5: FutureWarning: 

Passing `palette` without assigning `hue` is deprecated and will be removed in v0.14.0. Assign the `y` variable to `hue` and set `legend=False` for the same effect.



from matplotlib import pyplot as plt
import seaborn as sns
figsize = (12, 1.2 * len(_df_40['From'].unique()))
plt.figure(figsize=figsize)
sns.violinplot(_df_40, x='sender_id', y='From', inner='stick', palette='Dark2')
sns.despine(top=True, right=True, bottom=True, left=True)

In [53]:
#4️⃣ DATA FILTERING

In [71]:
#1 Remove Unnecessary Columns

filtered_df = cleaned_df[['From', 'To', 'Subject', 'Body', 'Date_utc']].copy()
filtered_df.head()

From  \
0                              
1            msagel@home.com   
2    slafontaine@globalp.com   
3    iceoperations@intcx.com   
4  jeff.youngflesh@enron.com   

                                                  To  \
0                                                      
1                                  jarnold@enron.com   
2                              john.arnold@enron.com   
3  icehelpdesk@intcx.com, internalmarketing@intcx...   
4  anthony.gilmore@enron.com, colleen.koenig@enro...   

                                             Subject  \
0                                                      
1                                             Status   
2                                 re:summer inverses   
3                      The WTI Bullet swap contracts   
4  Invitation: EBS/GSS Meeting w/Bristol Babcock ...   

                                                Body                  Date_utc  
0                                                                          NaT  
1  John:\n?\nI'm not really sure what happened be... 2000-11-16 17:30:00+00:00  
2  i suck-hope youve made more money in natgas la... 2000-12-08 13:05:00+00:00  
3  Hi,\n\n\nFollowing the e-mail you have receive... 2001-05-15 16:43:00+00:00  
4  Conference Room TBD.\n\nThis meeting will be t... 2000-11-27 09:49:00+00:00

In [57]:
#2 Drop Incomplete Records

filtered_df = filtered_df.dropna()
filtered_df.shape

(65486, 5)

In [58]:
#5️⃣ DATA ENRICHMENT

In [60]:
#1 Derived Fields

filtered_df['word_count'] = filtered_df['Body'].apply(lambda x: len(x.split()))
filtered_df[['word_count']].head()

word_count
1         104
2          51
3         170
4          29
5         137

from matplotlib import pyplot as plt
_df_41['index'].plot(kind='hist', bins=20, title='index')
plt.gca().spines[['top', 'right',]].set_visible(False)

from matplotlib import pyplot as plt
_df_42['word_count'].plot(kind='hist', bins=20, title='word_count')
plt.gca().spines[['top', 'right',]].set_visible(False)

from matplotlib import pyplot as plt
_df_43.plot(kind='scatter', x='index', y='word_count', s=32, alpha=.8)
plt.gca().spines[['top', 'right',]].set_visible(False)

from matplotlib import pyplot as plt
import seaborn as sns
def _plot_series(series, series_name, series_index=0):
  palette = list(sns.palettes.mpl_palette('Dark2'))
  xs = series['index']
  ys = series['word_count']
  
  plt.plot(xs, ys, label=series_name, color=palette[series_index % len(palette)])

fig, ax = plt.subplots(figsize=(10, 5.2), layout='constrained')
df_sorted = _df_44.sort_values('index', ascending=True)
_plot_series(df_sorted, '')
sns.despine(fig=fig, ax=ax)
plt.xlabel('index')
_ = plt.ylabel('word_count')

from matplotlib import pyplot as plt
import seaborn as sns
def _plot_series(series, series_name, series_index=0):
  palette = list(sns.palettes.mpl_palette('Dark2'))
  counted = (series['index']
                .value_counts()
              .reset_index(name='counts')
              .rename({'index': 'index'}, axis=1)
              .sort_values('index', ascending=True))
  xs = counted['index']
  ys = counted['counts']
  plt.plot(xs, ys, label=series_name, color=palette[series_index % len(palette)])

fig, ax = plt.subplots(figsize=(10, 5.2), layout='constrained')
df_sorted = _df_45.sort_values('index', ascending=True)
_plot_series(df_sorted, '')
sns.despine(fig=fig, ax=ax)
plt.xlabel('index')
_ = plt.ylabel('count()')

from matplotlib import pyplot as plt
_df_46['index'].plot(kind='line', figsize=(8, 4), title='index')
plt.gca().spines[['top', 'right']].set_visible(False)

from matplotlib import pyplot as plt
_df_47['word_count'].plot(kind='line', figsize=(8, 4), title='word_count')
plt.gca().spines[['top', 'right']].set_visible(False)

In [62]:
#2 Domain Extraction (Enrichment)

filtered_df['sender_domain'] = filtered_df['From'].apply(lambda x: x.split('@')[-1])
filtered_df[['From', 'sender_domain']].head()

From sender_domain
1            msagel@home.com      home.com
2    slafontaine@globalp.com   globalp.com
3    iceoperations@intcx.com     intcx.com
4  jeff.youngflesh@enron.com     enron.com
5  caroline.abramo@enron.com     enron.com

from matplotlib import pyplot as plt
_df_48['index'].plot(kind='hist', bins=20, title='index')
plt.gca().spines[['top', 'right',]].set_visible(False)

from matplotlib import pyplot as plt
import seaborn as sns
_df_49.groupby('From').size().plot(kind='barh', color=sns.palettes.mpl_palette('Dark2'))
plt.gca().spines[['top', 'right',]].set_visible(False)

from matplotlib import pyplot as plt
import seaborn as sns
_df_50.groupby('sender_domain').size().plot(kind='barh', color=sns.palettes.mpl_palette('Dark2'))
plt.gca().spines[['top', 'right',]].set_visible(False)

from matplotlib import pyplot as plt
import seaborn as sns
def _plot_series(series, series_name, series_index=0):
  palette = list(sns.palettes.mpl_palette('Dark2'))
  counted = (series['index']
                .value_counts()
              .reset_index(name='counts')
              .rename({'index': 'index'}, axis=1)
              .sort_values('index', ascending=True))
  xs = counted['index']
  ys = counted['counts']
  plt.plot(xs, ys, label=series_name, color=palette[series_index % len(palette)])

fig, ax = plt.subplots(figsize=(10, 5.2), layout='constrained')
df_sorted = _df_51.sort_values('index', ascending=True)
for i, (series_name, series) in enumerate(df_sorted.groupby('From')):
  _plot_series(series, series_name, i)
  fig.legend(title='From', bbox_to_anchor=(1, 1), loc='upper left')
sns.despine(fig=fig, ax=ax)
plt.xlabel('index')
_ = plt.ylabel('count()')

...

from matplotlib import pyplot as plt
import seaborn as sns
import pandas as pd
plt.subplots(figsize=(8, 8))
df_2dhist = pd.DataFrame({
    x_label: grp['sender_domain'].value_counts()
    for x_label, grp in _df_54.groupby('From')
})
sns.heatmap(df_2dhist, cmap='viridis')
plt.xlabel('From')
_ = plt.ylabel('sender_domain')

<string>:5: FutureWarning: 

Passing `palette` without assigning `hue` is deprecated and will be removed in v0.14.0. Assign the `y` variable to `hue` and set `legend=False` for the same effect.



from matplotlib import pyplot as plt
import seaborn as sns
figsize = (12, 1.2 * len(_df_55['From'].unique()))
plt.figure(figsize=figsize)
sns.violinplot(_df_55, x='index', y='From', inner='stick', palette='Dark2')
sns.despine(top=True, right=True, bottom=True, left=True)

<string>:5: FutureWarning: 

Passing `palette` without assigning `hue` is deprecated and will be removed in v0.14.0. Assign the `y` variable to `hue` and set `legend=False` for the same effect.



from matplotlib import pyplot as plt
import seaborn as sns
figsize = (12, 1.2 * len(_df_56['sender_domain'].unique()))
plt.figure(figsize=figsize)
sns.violinplot(_df_56, x='index', y='sender_domain', inner='stick', palette='Dark2')
sns.despine(top=True, right=True, bottom=True, left=True)

In [63]:
#6️⃣ DATA DEDUPLICATION

In [64]:
#1 Exact Match Deduplication

before = len(filtered_df)
filtered_df = filtered_df.drop_duplicates()
after = len(filtered_df)

print("Deduplicated:", before - after)

Deduplicated: 0


In [66]:
#2 Primary-Key Deduplication

filtered_df = filtered_df.drop_duplicates(subset=['From', 'Date_utc'])
filtered_df.head()

From  \
1            msagel@home.com   
2    slafontaine@globalp.com   
3    iceoperations@intcx.com   
4  jeff.youngflesh@enron.com   
5  caroline.abramo@enron.com   

                                                  To  \
1                                  jarnold@enron.com   
2                              john.arnold@enron.com   
3  icehelpdesk@intcx.com, internalmarketing@intcx...   
4  anthony.gilmore@enron.com, colleen.koenig@enro...   
5                             mike.grigsby@enron.com   

                                             Subject  \
1                                             Status   
2                                 re:summer inverses   
3                      The WTI Bullet swap contracts   
4  Invitation: EBS/GSS Meeting w/Bristol Babcock ...   
5                                       Harvard Mgmt   

                                                Body  \
1  John:\n?\nI'm not really sure what happened be...   
2  i suck-hope youve made more money in natgas la...   
3  Hi,\n\n\nFollowing the e-mail you have receive...   
4  Conference Room TBD.\n\nThis meeting will be t...   
5  Mike- I have their trader coming into the offi...   

                   Date_utc  word_count sender_domain  
1 2000-11-16 17:30:00+00:00         104      home.com  
2 2000-12-08 13:05:00+00:00          51   globalp.com  
3 2001-05-15 16:43:00+00:00         170     intcx.com  
4 2000-11-27 09:49:00+00:00          29     enron.com  
5 2000-12-12 17:33:00+00:00         137     enron.com

from matplotlib import pyplot as plt
_df_57['index'].plot(kind='hist', bins=20, title='index')
plt.gca().spines[['top', 'right',]].set_visible(False)

from matplotlib import pyplot as plt
_df_58['word_count'].plot(kind='hist', bins=20, title='word_count')
plt.gca().spines[['top', 'right',]].set_visible(False)

from matplotlib import pyplot as plt
import seaborn as sns
_df_59.groupby('From').size().plot(kind='barh', color=sns.palettes.mpl_palette('Dark2'))
plt.gca().spines[['top', 'right',]].set_visible(False)

from matplotlib import pyplot as plt
import seaborn as sns
_df_60.groupby('To').size().plot(kind='barh', color=sns.palettes.mpl_palette('Dark2'))
plt.gca().spines[['top', 'right',]].set_visible(False)

...

from matplotlib import pyplot as plt
import seaborn as sns
figsize = (12, 1.2 * len(_df_75['To'].unique()))
plt.figure(figsize=figsize)
sns.violinplot(_df_75, x='index', y='To', inner='stick', palette='Dark2')
sns.despine(top=True, right=True, bottom=True, left=True)

<string>:5: FutureWarning: 

Passing `palette` without assigning `hue` is deprecated and will be removed in v0.14.0. Assign the `y` variable to `hue` and set `legend=False` for the same effect.



from matplotlib import pyplot as plt
import seaborn as sns
figsize = (12, 1.2 * len(_df_76['Subject'].unique()))
plt.figure(figsize=figsize)
sns.violinplot(_df_76, x='index', y='Subject', inner='stick', palette='Dark2')
sns.despine(top=True, right=True, bottom=True, left=True)

<string>:5: FutureWarning: 

Passing `palette` without assigning `hue` is deprecated and will be removed in v0.14.0. Assign the `y` variable to `hue` and set `legend=False` for the same effect.



from matplotlib import pyplot as plt
import seaborn as sns
figsize = (12, 1.2 * len(_df_77['Body'].unique()))
plt.figure(figsize=figsize)
sns.violinplot(_df_77, x='index', y='Body', inner='stick', palette='Dark2')
sns.despine(top=True, right=True, bottom=True, left=True)

In [67]:
#7️⃣ DATA MASKING & SECURITY

In [69]:
#1 Mask Email Addresses

def mask_email(email):
    return email[:2] + "****@" + email.split('@')[-1]

filtered_df['from_masked'] = filtered_df['From'].apply(mask_email)
filtered_df[['From', 'from_masked']].head()

/tmp/ipython-input-3015376957.py:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  filtered_df['from_masked'] = filtered_df['From'].apply(mask_email)


From         from_masked
1            msagel@home.com     ms****@home.com
2    slafontaine@globalp.com  sl****@globalp.com
3    iceoperations@intcx.com    ic****@intcx.com
4  jeff.youngflesh@enron.com    je****@enron.com
5  caroline.abramo@enron.com    ca****@enron.com

from matplotlib import pyplot as plt
_df_78['index'].plot(kind='hist', bins=20, title='index')
plt.gca().spines[['top', 'right',]].set_visible(False)

from matplotlib import pyplot as plt
import seaborn as sns
_df_79.groupby('From').size().plot(kind='barh', color=sns.palettes.mpl_palette('Dark2'))
plt.gca().spines[['top', 'right',]].set_visible(False)

from matplotlib import pyplot as plt
import seaborn as sns
_df_80.groupby('from_masked').size().plot(kind='barh', color=sns.palettes.mpl_palette('Dark2'))
plt.gca().spines[['top', 'right',]].set_visible(False)

...

from matplotlib import pyplot as plt
import seaborn as sns
import pandas as pd
plt.subplots(figsize=(8, 8))
df_2dhist = pd.DataFrame({
    x_label: grp['from_masked'].value_counts()
    for x_label, grp in _df_84.groupby('From')
})
sns.heatmap(df_2dhist, cmap='viridis')
plt.xlabel('From')
_ = plt.ylabel('from_masked')

<string>:5: FutureWarning: 

Passing `palette` without assigning `hue` is deprecated and will be removed in v0.14.0. Assign the `y` variable to `hue` and set `legend=False` for the same effect.



from matplotlib import pyplot as plt
import seaborn as sns
figsize = (12, 1.2 * len(_df_85['From'].unique()))
plt.figure(figsize=figsize)
sns.violinplot(_df_85, x='index', y='From', inner='stick', palette='Dark2')
sns.despine(top=True, right=True, bottom=True, left=True)

<string>:5: FutureWarning: 

Passing `palette` without assigning `hue` is deprecated and will be removed in v0.14.0. Assign the `y` variable to `hue` and set `legend=False` for the same effect.



from matplotlib import pyplot as plt
import seaborn as sns
figsize = (12, 1.2 * len(_df_86['from_masked'].unique()))
plt.figure(figsize=figsize)
sns.violinplot(_df_86, x='index', y='from_masked', inner='stick', palette='Dark2')
sns.despine(top=True, right=True, bottom=True, left=True)

In [72]:
#2 Hashing

import hashlib

filtered_df['from_hash'] = filtered_df['From'].apply(
    lambda x: hashlib.sha256(x.encode()).hexdigest()
)

filtered_df[['from_hash']].head()

from_hash
0  e3b0c44298fc1c149afbf4c8996fb92427ae41e4649b93...
1  17f17dd4074f3955606b951741ea785f2360278b50488a...
2  b35c238d5a30faf4834ebd80d93a72b8e365795c57493e...
3  b633b679b3fe3255dddd3f6589837bc4a4d7e717f64fd7...
4  4cc1213fff277a44aebb500d15668e0876e7cd698b8008...

from matplotlib import pyplot as plt
import seaborn as sns
_df_87.groupby('from_hash').size().plot(kind='barh', color=sns.palettes.mpl_palette('Dark2'))
plt.gca().spines[['top', 'right',]].set_visible(False)

In [73]:
#8️⃣ DATA STANDARDIZATION

In [74]:
filtered_df.columns = [c.lower().replace(" ", "_") for c in filtered_df.columns]
filtered_df.head()

from  \
0                              
1            msagel@home.com   
2    slafontaine@globalp.com   
3    iceoperations@intcx.com   
4  jeff.youngflesh@enron.com   

                                                  to  \
0                                                      
1                                  jarnold@enron.com   
2                              john.arnold@enron.com   
3  icehelpdesk@intcx.com, internalmarketing@intcx...   
4  anthony.gilmore@enron.com, colleen.koenig@enro...   

                                             subject  \
0                                                      
1                                             Status   
2                                 re:summer inverses   
3                      The WTI Bullet swap contracts   
4  Invitation: EBS/GSS Meeting w/Bristol Babcock ...   

                                                body  \
0                                                      
1  John:\n?\nI'm not really sure what happened be...   
2  i suck-hope youve made more money in natgas la...   
3  Hi,\n\n\nFollowing the e-mail you have receive...   
4  Conference Room TBD.\n\nThis meeting will be t...   

                   date_utc                                          from_hash  
0                       NaT  e3b0c44298fc1c149afbf4c8996fb92427ae41e4649b93...  
1 2000-11-16 17:30:00+00:00  17f17dd4074f3955606b951741ea785f2360278b50488a...  
2 2000-12-08 13:05:00+00:00  b35c238d5a30faf4834ebd80d93a72b8e365795c57493e...  
3 2001-05-15 16:43:00+00:00  b633b679b3fe3255dddd3f6589837bc4a4d7e717f64fd7...  
4 2000-11-27 09:49:00+00:00  4cc1213fff277a44aebb500d15668e0876e7cd698b8008...

In [75]:
#9️⃣ ERROR HANDLING & LOGGING

In [76]:
error_log = []

try:
    pd.to_datetime("invalid-date")
except Exception as e:
    error_log.append(str(e))

error_log

['Unknown datetime string format, unable to parse: invalid-date, at position 0']

In [82]:
error_log = []

def safe_to_datetime(value, column_name="unknown"):
    try:
        return pd.to_datetime(value)
    except Exception as e:
        error_log.append({
            "column": column_name,
            "value": value,
            "error": str(e)
        })
        return pd.NaT

In [77]:
#🔟 METADATA HANDLING

In [78]:
filtered_df['ingestion_time'] = datetime.utcnow()
filtered_df['source_system'] = 'Enron Email Dataset'
filtered_df['data_version'] = 'v1.0'

filtered_df[['ingestion_time', 'source_system', 'data_version']].head()

/tmp/ipython-input-3829850487.py:1: DeprecationWarning: datetime.datetime.utcnow() is deprecated and scheduled for removal in a future version. Use timezone-aware objects to represent datetimes in UTC: datetime.datetime.now(datetime.UTC).
  filtered_df['ingestion_time'] = datetime.utcnow()


ingestion_time        source_system data_version
0 2026-01-09 07:39:22.050037  Enron Email Dataset         v1.0
1 2026-01-09 07:39:22.050037  Enron Email Dataset         v1.0
2 2026-01-09 07:39:22.050037  Enron Email Dataset         v1.0
3 2026-01-09 07:39:22.050037  Enron Email Dataset         v1.0
4 2026-01-09 07:39:22.050037  Enron Email Dataset         v1.0

from matplotlib import pyplot as plt
_df_88['index'].plot(kind='hist', bins=20, title='index')
plt.gca().spines[['top', 'right',]].set_visible(False)

from matplotlib import pyplot as plt
import seaborn as sns
def _plot_series(series, series_name, series_index=0):
  palette = list(sns.palettes.mpl_palette('Dark2'))
  counted = (series['index']
                .value_counts()
              .reset_index(name='counts')
              .rename({'index': 'index'}, axis=1)
              .sort_values('index', ascending=True))
  xs = counted['index']
  ys = counted['counts']
  plt.plot(xs, ys, label=series_name, color=palette[series_index % len(palette)])

fig, ax = plt.subplots(figsize=(10, 5.2), layout='constrained')
df_sorted = _df_89.sort_values('index', ascending=True)
_plot_series(df_sorted, '')
sns.despine(fig=fig, ax=ax)
plt.xlabel('index')
_ = plt.ylabel('count()')

from matplotlib import pyplot as plt
import seaborn as sns
def _plot_series(series, series_name, series_index=0):
  palette = list(sns.palettes.mpl_palette('Dark2'))
  counted = (series['ingestion_time']
                .value_counts()
              .reset_index(name='counts')
              .rename({'index': 'ingestion_time'}, axis=1)
              .sort_values('ingestion_time', ascending=True))
  xs = counted['ingestion_time']
  ys = counted['counts']
  plt.plot(xs, ys, label=series_name, color=palette[series_index % len(palette)])

fig, ax = plt.subplots(figsize=(10, 5.2), layout='constrained')
df_sorted = _df_90.sort_values('ingestion_time', ascending=True)
_plot_series(df_sorted, '')
sns.despine(fig=fig, ax=ax)
plt.xlabel('ingestion_time')
_ = plt.ylabel('count()')

from matplotlib import pyplot as plt
_df_91['index'].plot(kind='line', figsize=(8, 4), title='index')
plt.gca().spines[['top', 'right']].set_visible(False)

In [79]:
#1️⃣1️⃣ SAMPLING

In [80]:
sample_df = filtered_df.sample(n=5, random_state=42)
sample_df

from  \
86955     kevin.brady@enron.com   
41227  vince.kaminski@enron.com   
35370  vince.kaminski@enron.com   
59692    beth.cherry@enform.com   
74186  david.delainey@enron.com   

                                                      to  \
86955                                 jeffsmirin@txu.com   
41227                                  vkaminski@aol.com   
35370  lance.cunningham@enron.com, vasant.shanbhogue@...   
59692                              jason.wolfe@enron.com   
74186                              kay.chapman@enron.com   

                                                 subject  \
86955                                          Smart Pig   
41227  Vince Kaminski's "Bio" and requirements for th...   
35370                         ENRON: WEFA luncheon May 1   
59692                               Will you go with me?   
74186                        Jordan Mintz expense report   

                                                    body  \
86955  Jeff,\n\nI have two questions for you, first, ...   
41227  ---------------------- Forwarded by Vince J Ka...   
35370  Would you like to attend the presentation and ...   
59692  OK, now we are getting down to the details...\...   
74186  ---------------------- Forwarded by David W De...   

                       date_utc  \
86955 2002-06-13 13:43:59+00:00   
41227 2001-04-14 01:32:00+00:00   
35370 2001-04-11 12:36:00+00:00   
59692 2001-07-27 22:08:04+00:00   
74186 2000-06-09 18:23:00+00:00   

                                               from_hash  \
86955  efe57bee116a4155476a94274ee6346aad9b58f167ab7f...   
41227  267e67c288830694202b01c68fa9c4ed1f4921da0bf0d1...   
35370  267e67c288830694202b01c68fa9c4ed1f4921da0bf0d1...   
59692  204e9fac5873952ff9801133267562af8ff27cf1b97906...   
74186  73b65ad601bee5aa6647a08ae886f39fc97959e3afa62a...   

                  ingestion_time        source_system data_version  
86955 2026-01-09 07:39:22.050037  Enron Email Dataset         v1.0  
41227 2026-01-09 07:39:22.050037  Enron Email Dataset         v1.0  
35370 2026-01-09 07:39:22.050037  Enron Email Dataset         v1.0  
59692 2026-01-09 07:39:22.050037  Enron Email Dataset         v1.0  
74186 2026-01-09 07:39:22.050037  Enron Email Dataset         v1.0

In [84]:
filtered_df.to_csv('final_ingested_enron_emails.csv', index=False)
monthly_counts.to_csv('monthly_email_aggregation.csv', index=False)